```
--- Day 3: Gear Ratios ---
You and the Elf eventually reach a gondola lift station; he says the gondola lift will take you up to the water source, but this is as far as he can bring you. You go inside.

It doesn't take long to find the gondolas, but there seems to be a problem: they're not moving.

"Aaah!"

You turn around to see a slightly-greasy Elf with a wrench and a look of surprise. "Sorry, I wasn't expecting anyone! The gondola lift isn't working right now; it'll still be a while before I can fix it." You offer to help.

The engineer explains that an engine part seems to be missing from the engine, but nobody can figure out which one. If you can add up all the part numbers in the engine schematic, it should be easy to work out which part is missing.

The engine schematic (your puzzle input) consists of a visual representation of the engine. There are lots of numbers and symbols you don't really understand, but apparently any number adjacent to a symbol, even diagonally, is a "part number" and should be included in your sum. (Periods (.) do not count as a symbol.)

Here is an example engine schematic:

467..114..
...*......
..35..633.
......#...
617*......
.....+.58.
..592.....
......755.
...$.*....
.664.598..
In this schematic, two numbers are not part numbers because they are not adjacent to a symbol: 114 (top right) and 58 (middle right). Every other number is adjacent to a symbol and so is a part number; their sum is 4361.

Of course, the actual engine schematic is much larger. What is the sum of all of the part numbers in the engine schematic?
```

In [ ]:
let inputLines = System.IO.File.ReadAllLines "input/3.txt"

type Transform = {
    x: int
    y: int
}



type Part = {
    positions: Transform list
    partNumber: int
}

type Symbol = {
    transform: Transform
    symbol: char
}

type ChartEntity = Part of Part | Symbol of Symbol

let continuePart (y: int) (x: int) (nextDigit: int) (part: Part) : Part =
    {positions = {x=x; y=y} :: part.positions; partNumber = part.partNumber * 10 + nextDigit}

let (|Integer|_|) (c: char) =
    match System.Int32.TryParse (string c) with
    | true, i -> Some i
    | _ -> None

let rec findPartsOnALine (y: int) (x: int) (previous: ChartEntity list) (current: ChartEntity option) (remaining: char list) : ChartEntity list =
    match remaining, current with
    | '.' :: rest, None -> findPartsOnALine y (x + 1) previous None rest
    | '.' :: rest, Some e -> findPartsOnALine y (x + 1) (e :: previous) None rest
    | Integer c :: rest, None -> findPartsOnALine y (x + 1) previous (Some (Part ({positions = [{x=x; y=y}]; partNumber = c}))) rest
    | Integer c :: rest, Some (Part part) -> findPartsOnALine y (x + 1) previous (Some (Part (continuePart y x c part))) rest
    | Integer c :: rest, Some (Symbol symbol) -> findPartsOnALine y (x + 1) (symbol :: previous) (Some (Part ({positions = [{x=x; y=y}]; partNumber = c}))) rest
    | c :: rest, None -> findPartsOnALine y (x + 1) (Symbol {transform = {x=x; y=y}; symbol = c} :: previous) None rest
    | c :: rest, Some e -> findPartsOnALine y (x + 1) (e :: previous) (Some (Symbol {transform = {x=x; y=y}; symbol = c})) rest
    | [], Some e -> findPartsOnALine y x (e :: previous) None []
    | [], None -> previous |> List.rev

let chartEntities = inputLines |> Array.mapi (fun y line -> findPartsOnALine y 0 [] None (line |> Seq.toList)) |> List.ofArray |> List.concat

let chebyshevDistance (t1: Transform) (t2: Transform) =
    max (abs (t2.x - t1.x)) (abs (t2.y - t1.y))

let isNextTo (t1: Transform) (t2: Transform) =
    chebyshevDistance t1 t2 = 1

let findNeighbourPartForSymbol (symbol: Symbol) (parts: Part list) =
    parts |> List.filter (fun part -> part.positions |> List.exists (fun position -> isNextTo position symbol.transform))

let allSymbols = chartEntities |> List.choose (function | Symbol s -> Some s | _ -> None)

let allParts = chartEntities |> List.choose (function | Part p -> Some p | _ -> None)

let allPartsNeighbouringSymbols = allSymbols |> List.map (fun symbol -> symbol, findNeighbourPartForSymbol symbol allParts)

display allPartsNeighbouringSymbols

allPartsNeighbouringSymbols |> List.map snd |> List.concat |> List.distinct |> List.sumBy (fun part -> part.partNumber)

for (symbol, parts) in allPartsNeighbouringSymbols do
    printfn "%c: %A" symbol.symbol symbol.transform
    for part in parts do
        printfn "    %d" part.partNumber


[ ({ transform = { x = 38
 y = 1 }
 symbol = '+' }, [{ positions = [{ x = 39
 y = 0 }; { x = 38
 y = 0 }; { x = 37
 y = 0 }]
 partNumber = 858 }]), ({ transform = { x = 75
 y = 1 }
 symbol = '*' }, [{ positions = [{ x = 77
 y = 0 }; { x = 76
 y = 0 }; { x = 75
 y = 0 }]
 partNumber = 801 }; { positions = [{ x = 74
 y = 2 }; { x = 73
 y = 2 }; { x = 72
 y = 2 }]
 partNumber = 691 }]), ({ transform = { x = 85
 y = 1 }
 symbol = '+' }, [{ positions = [{ x = 88
 y = 0 }; { x = 87
 y = 0 }; { x = 86
 y = 0 }]
 partNumber = 487 }]), ({ transform = { x = 3
 y = 2 }
 symbol = '*' }, [{ positions = [{ x = 2
 y = 1 }; { x = 1
 y = 1 }; { x = 0
 y = 1 }]
 partNumber = 436 }; { positions = [{ x = 6
 y = 2 }; { x = 5
 y = 2 }; { x = 4
 y = 2 }]
 partNumber = 982 }]), ({ transform = { x = 18
 y = 2 }
 symbol = '=' }, [{ positions = [{ x = 21
 y = 3 }; { x = 20
 y = 3 }; { x = 19
 y = 3 }]
 partNumber = 588 }]), ({ transform = { x = 29
 y = 2 }
 symbol = '=' }, [{ positions = [{ x = 30
 y = 1 }; { x = 29
 y = 1 }; { x = 28
 y = 1 }]
 partNumber = 140 }]), ({ transform = { x = 56
 y = 2 }
 symbol = '*' }, [{ positions = [{ x = 55
 y = 2 }; { x = 54
 y = 2 }; { x = 53
 y = 2 }]
 partNumber = 375 }; { positions = [{ x = 59
 y = 3 }; { x = 58
 y = 3 }; { x = 57
 y = 3 }]
 partNumber = 631 }]), ({ transform = { x = 61
 y = 2 }
 symbol = '=' }, [{ positions = [{ x = 61
 y = 1 }; { x = 60
 y = 1 }; { x = 59
 y = 1 }]
 partNumber = 859 }]), ({ transform = { x = 77
 y = 2 }
 symbol = '-' }, [{ positions = [{ x = 78
 y = 3 }; { x = 77
 y = 3 }; { x = 76
 y = 3 }]
 partNumber = 952 }]), ({ transform = { x = 98
 y = 2 }
 symbol = '*' }, [{ positions = [{ x = 98
 y = 3 }; { x = 97
 y = 3 }; { x = 96
 y = 3 }]
 partNumber = 661 }]), ({ transform = { x = 37
 y = 3 }
 symbol = '*' }, [{ positions = [{ x = 36
 y = 2 }; { x = 35
 y = 2 }; { x = 34
 y = 2 }]
 partNumber = 203 }; { positions = [{ x = 38
 y = 4 }; { x = 37
 y = 4 }; { x = 36
 y = 4 }]
 partNumber = 917 }]), ({ transform = { x = 50
 y = 3 }
 symbol = '*' }, [{ positions = [{ x = 49
 y = 2 }; { x = 48
 y = 2 }; { x = 47
 y = 2 }]
 partNumber = 263 }; { positions = [{ x = 49
 y = 4 }; { x = 48
 y = 4 }; { x = 47
 y = 4 }]
 partNumber = 375 }]), ({ transform = { x = 68
 y = 3 }
 symbol = '*' }, [{ positions = [{ x = 67
 y = 2 }; { x = 66
 y = 2 }; { x = 65
 y = 2 }]
 partNumber = 402 }]), ({ transform = { x = 109
 y = 3 }
 symbol = '=' }, [{ positions = [{ x = 111
 y = 2 }; { x = 110
 y = 2 }; { x = 109
 y = 2 }]
 partNumber = 575 }]), ({ transform = { x = 122
 y = 3 }
 symbol = '*' }, [{ positions = [{ x = 125
 y = 3 }; { x = 124
 y = 3 }; { x = 123
 y = 3 }]
 partNumber = 333 }; { positions = [{ x = 121
 y = 4 }; { x = 120
 y = 4 }; { x = 119
 y = 4 }]
 partNumber = 664 }]), ({ transform = { x = 15
 y = 4 }
 symbol = '*' }, [{ positions = [{ x = 15
 y = 3 }; { x = 14
 y = 3 }; { x = 13
 y = 3 }]
 partNumber = 114 }; { positions = [{ x = 16
 y = 5 }; { x = 15
 y = 5 }; { x = 14
 y = 5 }]
 partNumber = 452 }]), ({ transform = { x = 40
 y = 4 }
 symbol = '&' }, [{ positions = [{ x = 42
 y = 5 }; { x = 41
 y = 5 }; { x = 40
 y = 5 }]
 partNumber = 969 }]), ({ transform = { x = 87
 y = 4 }
 symbol = '*' }, [{ positions = [{ x = 88
 y = 3 }; { x = 87
 y = 3 }]
 partNumber = 14 }; { positions = [{ x = 86
 y = 5 }; { x = 85
 y = 5 }; { x = 84
 y = 5 }]
 partNumber = 941 }]), ({ transform = { x = 106
 y = 4 }
 symbol = '*' }, [{ positions = [{ x = 105
 y = 4 }; { x = 104
 y = 4 }; { x = 103
 y = 4 }]
 partNumber = 544 }; { positions = [{ x = 109
 y = 5 }; { x = 108
 y = 5 }; { x = 107
 y = 5 }]
 partNumber = 427 }]), ({ transform = { x = 114
 y = 4 }
 symbol = '*' }, [{ positions = [{ x = 115
 y = 3 }; { x = 114
 y = 3 }; { x = 113
 y = 3 }]
 partNumber = 706 }; { positions = [{ x = 113
 y = 5 }; { x = 112
 y = 5 }; { x = 111
 y = 5 }]
 partNumber = 728 }]) ... (more) ] HeadOrDefault ({ transform = { x = 38\n y = 1 }\n symbol = '+' }, [{ positions = [{ x = 39\n y = 0 }; { x = 38\n y = 0 }; { x = 37\n y = 0

+: { x = 38
  y = 1 }
    858
*: { x = 75
  y = 1 }
    801
    691
+: { x = 85
  y = 1 }
    487
*: { x = 3
  y = 2 }
    436
    982
=: { x = 18
  y = 2 }
    588
=: { x = 29
  y = 2 }
    140
*: { x = 56
  y = 2 }
    375
    631
=: { x = 61
  y = 2 }
    859
-: { x = 77
  y = 2 }
    952
*: { x = 98
  y = 2 }
    661
*: { x = 37
  y = 3 }
    203
    917
*: { x = 50
  y = 3 }
    263
    375
*: { x = 68
  y = 3 }
    402
=: { x = 109
  y = 3 }
    575
*: { x = 122
  y = 3 }
    333
    664
*: { x = 15
  y = 4 }
    114
    452
&: { x = 40
  y = 4 }
    969
*: { x = 87
  y = 4 }
    14
    941
*: { x = 106
  y = 4 }
    544
    427
*: { x = 114
  y = 4 }
    706
    728
*: { x = 3
  y = 5 }
    194
    243
*: { x = 33
  y = 5 }
    743
    470
#: { x = 45
  y = 5 }
    145
*: { x = 55
  y = 5 }
    309
    111
/: { x = 72
  y = 5 }
    259
*: { x = 12
  y = 6 }
    807
    130
*: { x = 67
  y = 6 }
    659
    199
+: { x = 80
  y = 6 }
    873
*: { x = 89
  y = 6 }
    828
    640
%